In [52]:
from backtesting import Backtest, Strategy
from backtesting.lib import crossover, SignalStrategy, TrailingStrategy
from backtesting.test import SMA
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
import numpy as np
import pandas as pd
import os, glob

In [124]:
INDEX_CLASS_3 = 4
INDEX_CLASS_5 = 5

#LOAD DATASET
cwd = os.getcwd()
#source_data = os.path.join(cwd, r'forex historic/dukascopy/2018/')
source_data = os.path.join(cwd, r'../../Datasets/EURUSD/ene2004_nov2019')
filenames = glob.glob(source_data + "/*.csv")
filenames.sort()
for file in filenames:
    print(os.path.basename(file))
DF_EURUSD_ASK = pd.read_csv(filenames[INDEX_CLASS_5], index_col=None, parse_dates=True, header=0)

DF_EURUSD_ASK = DF_EURUSD_ASK.iloc[0:6240,:]#Un Año 6240
print(DF_EURUSD_ASK.head())
print(DF_EURUSD_ASK.shape)

EURUSD_ASK_01.01.2004-19.11.2019.csv
EURUSD_ASK_1_D_01.01.2004-19.11.2019.csv
EURUSD_ASK_1_H_01.01.2004-19.11.2019.csv
EURUSD_ASK_4_h_31.12.2003-18.11.2019.csv
procesado.csv
procesado5.csv
              Datetime     Open     High      Low    Close      Volume  \
0  2004-01-01 00:00:00  1.25950  1.25960  1.25826  1.25910   6654.2002   
1  2004-01-01 01:00:00  1.25958  1.25960  1.25947  1.25951    660.6000   
2  2004-01-01 02:00:00  1.25955  1.25962  1.25944  1.25951   2091.0000   
3  2004-01-01 03:00:00  1.25950  1.25965  1.25834  1.25869  10003.0996   
4  2004-01-01 04:00:00  1.25908  1.25960  1.25843  1.25950   7603.3999   

   Pct_Range    HL_PCT  Class  Sell  Sell2  Buy  Buy2  
0   0.000326  0.106425      0   NaN    NaN  NaN   NaN  
1   0.000000  0.010321      0   NaN    NaN  NaN   NaN  
2  -0.000651  0.014291      0   NaN    NaN  NaN   NaN  
3   0.000644  0.104076      0   NaN    NaN  NaN   NaN  
4   0.000040  0.092894      0   NaN    NaN  NaN   NaN  
(6240, 13)


In [132]:
#Estrategia para usar con solo 3 Clases
# 1 es compra, -1 es venta
# se revisa si hay una orden previa abiera o no, si no hay operacion y el indicador es de compra 
# venta, entonces se ejecuta

# Si existe una operacion entonces se evalua si es diferente la siuiente Operacion se cierra y abre otra.

# Si hay Operacion abierta y el indicador actual es 0 entonces solo se cierra la operacion. 
class MAW3(Strategy):
    def init(self):
        self.Operation = self.data.Class
        self.Close = self.data.Close
        self.Buy = self.data.Buy
        self.Sell = self.data.Sell
        print(self.Operation)

                
    def next(self):        
        operation = self.data.Class[-1]
        price = self.data.Close[-1]
        time = self.data.Datetime[-1]
        print(price)
        if not self.position:
            if (operation == -1):
                self.sell()
                print(operation, 'SELL at close: ', price, time)
            elif (operation == 1):
                self.buy()
                print(operation, 'BUY at close: ', price, time)
        else:
            # Compra Largo
            # tenemos compra y la actual es venta:
            if (self.position.is_long and operation == -1):
                self.position.close() # Se cierra 
                self.sell() # Y se abre venta
                print(operation, 'SELL at close: ', price, time)
            # Si estamos en compra y hay compra, compramos
            elif self.position.is_long and operation == 1:
                self.buy()
                print(operation, 'BUY at close: ', price, time)
            elif self.position.is_long and operation ==0 :
                self.position.close()
                #oldPrice = self.data.Close[-2]
                #oldTime = self.data.Datetime[-2]
                #print('    ', operation, ' at close:', price, time)
                #print('    Current price= ',price, 'at time: ', time)
                #print('    Previews price=',oldPrice, ' at time: ', oldTime)
                #if price <= oldPrice:
                #    print('        CLOSE Position Current price= ',price, 'less than: ', oldPrice)
                #    self.position.close()

            # Venta Corto
            # Si teniamos venta y ahora es compra
            elif (self.position.is_short and operation == 1):
                self.position.close() # Se cierra
                self.buy # y se abre compra
                print(operation, 'BUY at close: ', price, time)
            # Si hay venta y es venta, se hace venta
            elif self.position.is_short and operation == -1:
                self.sell()
                print(operation, 'SELL at close: ', price, time)
            elif self.position.is_short and operation == 0:
                self.position.close()
                #oldPrice = self.data.Close[-2]
                #oldTime = self.data.Datetime[-2]
                #print('    ', operation, ' at close:', price, time)
                #print('    Current price= ',price, 'at time: ', time)
                #print('    Previews price=',oldPrice, ' at time: ', oldTime)
                #if price >= oldPrice:
                #    print('        CLOSE Position Current price= ',price, 'less than: ', oldPrice)
                #    self.position.close()
            #else:
            #    self.position.close()
        
            
class MAW5(Strategy):
    def init(self):
        self.Operation = self.data.Class
        self.Close = self.data.Close
        self.Buy = self.data.Buy
        self.Sell = self.data.Sell
        print(self.Operation)

                
    def next(self):        
        operation = self.data.Class[-1]
        prev_operation = self.data.Class[-2]
        price = self.data.Close[-1]
        prev_price = self.data.Close[-2]
        time = self.data.Datetime[-1]
        print(self.data.Close)
        
        
        if not self.position:
            if (operation == -1 or operation == -2):
                self.sell()
                print(operation, 'SELL with OP at close: ', price, time)
            elif (operation == 1 or operation == 2):
                self.buy()
                print(operation, 'BUY without OP at close: ', price, time)
                print(operation, 'position: ', self.position)
        else:
            # Compra Largo
            # tenemos compra:
            if (self.position.is_long):
                print('LARGA', operation, ' at close:', price, time)
                #si la siguiente es compra 2 o compra 1
                if (operation == 2 or operation ==1):
                    self.buy() #Compra nuevamente
                    print('        COMPRA', operation, ' at close:', price, time)
                #Si el indicador es hold
                elif (operation == 0):
                    #si el precio actual es menor que hace 1 tiempo
                    if (price < prev_price):
                        print('            HOLD', operation, ' at close:', price, time, 'prev price', prev_price)
                        self.position.close() # Se cierra 
                # Si la operacion es de venta osea -1 o -2 
                elif (operation == -1 or operation == -2):
                    print('        OP CONTRARIA SE ABRE VENTA', operation, ' at close:', price, time)
                    self.position.close()# se cierra 
                    self.sell() # Y se abre venta

            # Venta Corto
            # Si teniamos venta y ahora es compra
            elif (self.position.is_short):      
                print('CORTA', operation, ' at close:', price, time)
                #si la siguiente es Venta 2 o venta 1
                if (operation == -2 or operation == -1):
                    self.sell() #Compra nuevamente
                    print('        VENTA', operation, ' at close:', price, time)
                #Si el indicador es hold
                elif (operation == 0):
                    print('        HOLD', operation, ' at close:', price, time)
                    #si el precio actual es mayor que hace 1 tiempo
                    if (price > prev_price):
                        print(price, ' price')
                        print(prev_price,' prev_price')
                        print('            HOLD', operation, ' at close:', price, time, 'prev price', prev_price)
                        self.position.close() # Se cierra 
                # Si la operacion es de compra osea 1 o 2 
                elif (operation == 1 or operation == 2):
                    print('        OP CONTRARIA SE ABRE COMPRA', operation, ' at close:', price, time)
                    self.position.close()# se cierra 
                    self.buy() 
                    #self.buy() # Y se abre venta

            
class ONLY2(Strategy):
    def init(self):
        self.Operation = self.data.Class
        self.Close = self.data.Close
        self.Buy = self.data.Buy
        self.Sell = self.data.Sell
        print(self.Operation)

                
    def next(self):        
        operation = self.data.Class[-1]
        prev_operation = self.data.Class[-2]
        price = self.data.Close[-1]
        time = self.data.Datetime[-1]
        print(price)
        
        if not self.position:
            if (operation == -2):
                self.sell()
                print(operation, 'SELL at close: ', price, time)
            elif (operation == 2):
                self.buy()
                print(operation, 'BUY at close: ', price, time)
        else:
            # Compra Largo
            # tenemos compra y la actual es venta:
            if (self.position.is_long and (operation == -2 or operation == -1)):
                self.position.close() # Se cierra 
                self.sell() # Y se abre venta
                print(operation, 'SELL at close: ', price, time)
            # Si estamos en compra y hay compra, compramos
            elif self.position.is_long and operation == 2:
                self.buy()
                print(operation, 'BUY at close: ', price, time)
            elif self.position.is_long and operation == 0:
                self.position.close()
                #oldPrice = self.data.Close[-2]
                #oldTime = self.data.Datetime[-2]
                #print('    ', operation, ' at close:', price, time)
                #print('    Current price= ',price, 'at time: ', time)
                #print('    Previews price=',oldPrice, ' at time: ', oldTime)
                #if price <= oldPrice:
                #    print('        CLOSE Position Current price= ',price, 'less than: ', oldPrice)
                #    self.position.close()

            # Venta Corto
            # Si teniamos venta y ahora es compra
            elif (self.position.is_short and operation == 2):
                self.position.close() # Se cierra
                self.buy # y se abre compra
                print(operation, 'BUY at close: ', price, time)
            # Si hay venta y es venta, se hace venta
            elif self.position.is_short and (operation == -2 or operation == -1):
                self.sell()
                print(operation, 'SELL at close: ', price, time)
            elif self.position.is_short and operation == 0:
                if prev_operation == -1:
                    self.position.close()
                #oldPrice = self.data.Close[-2]
                #oldTime = self.data.Datetime[-2]
                #print('    ', operation, ' at close:', price, time)
                #print('    Current price= ',price, 'at time: ', time)
                #print('    Previews price=',oldPrice, ' at time: ', oldTime)
                #if price >= oldPrice:
                #    print('        CLOSE Position Current price= ',price, 'less than: ', oldPrice)
                #    self.position.close()
            #else:
            #    self.position.close()
        
                
                
#class composable(SignalStrategy, TrailingStrategy):
#    def init(self):
#        super().init()
#        self.set_signal(self.data.position)
#        self.set_trailing_sl(1)
        

In [133]:
#bt = Backtest(DF_EURUSD_ASK, MAW3, cash=1000, commission=.0001)
bt = Backtest(DF_EURUSD_ASK, MAW5, cash=1000, commission=.0000)
#bt = Backtest(DF_EURUSD_ASK, ONLY2, cash=1000, commission=.0001)
bt.run()

/Users/marami3/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: UserWarning: Data index is not datetime. Assuming simple periods.
  


[ 0  0  0 ... -1  0  1]
[1.2591  1.25951]
[1.2591  1.25951 1.25951]
[1.2591  1.25951 1.25951 1.25869]
[1.2591  1.25951 1.25951 1.25869 1.2595 ]
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955]
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948]
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591 ]
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591  1.25907]
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591  1.25907
 1.25917]
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591  1.25907
 1.25917 1.25911]
-1 SELL with OP at close:  1.25911 2004-01-01 10:00:00
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591  1.25907
 1.25917 1.25911 1.25785]
CORTA 1  at close: 1.25785 2004-01-01 11:00:00
        OP CONTRARIA SE ABRE COMPRA 1  at close: 1.25785 2004-01-01 11:00:00
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591  1.25907
 1.25917 1.25911 1.25785 1.26029]
LARGA -1  at close: 1.26029 2004-01-01 12:00:00
 

 1.2721  1.27469 1.2741 ]
LARGA 1  at close: 1.2741 2004-01-06 11:00:00
        COMPRA 1  at close: 1.2741 2004-01-06 11:00:00
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591  1.25907
 1.25917 1.25911 1.25785 1.26029 1.25903 1.25943 1.25911 1.25909 1.25697
 1.2539  1.25461 1.25411 1.25454 1.2565  1.25733 1.25675 1.25535 1.25308
 1.2563  1.25607 1.25577 1.25698 1.25733 1.2591  1.26202 1.2619  1.26003
 1.25912 1.25999 1.26131 1.25846 1.25911 1.26    1.25916 1.25875 1.25904
 1.25832 1.26077 1.26318 1.26554 1.26569 1.26534 1.26605 1.26616 1.26554
 1.26634 1.26847 1.26354 1.26527 1.26662 1.26807 1.26709 1.26454 1.26661
 1.26717 1.26792 1.26833 1.26608 1.26696 1.2656  1.26753 1.26737 1.2683
 1.26805 1.26669 1.26818 1.26779 1.2677  1.26874 1.27033 1.27094 1.27127
 1.2721  1.27469 1.2741  1.27544]
LARGA 1  at close: 1.27544 2004-01-06 12:00:00
        COMPRA 1  at close: 1.27544 2004-01-06 12:00:00
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591  1.25907
 1.2591

 1.27219 1.27699 1.27695 1.27572 1.27594 1.27649]
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591  1.25907
 1.25917 1.25911 1.25785 1.26029 1.25903 1.25943 1.25911 1.25909 1.25697
 1.2539  1.25461 1.25411 1.25454 1.2565  1.25733 1.25675 1.25535 1.25308
 1.2563  1.25607 1.25577 1.25698 1.25733 1.2591  1.26202 1.2619  1.26003
 1.25912 1.25999 1.26131 1.25846 1.25911 1.26    1.25916 1.25875 1.25904
 1.25832 1.26077 1.26318 1.26554 1.26569 1.26534 1.26605 1.26616 1.26554
 1.26634 1.26847 1.26354 1.26527 1.26662 1.26807 1.26709 1.26454 1.26661
 1.26717 1.26792 1.26833 1.26608 1.26696 1.2656  1.26753 1.26737 1.2683
 1.26805 1.26669 1.26818 1.26779 1.2677  1.26874 1.27033 1.27094 1.27127
 1.2721  1.27469 1.2741  1.27544 1.27952 1.27692 1.27456 1.27717 1.27669
 1.27626 1.27623 1.2739  1.27256 1.27257 1.2715  1.27192 1.27032 1.27068
 1.27134 1.272   1.27175 1.27227 1.27045 1.26623 1.26673 1.26637 1.26604
 1.26801 1.2688  1.26815 1.26934 1.26632 1.26684 1.26518 1.26454 1.26376
 1

 1.27586 1.27436 1.27891 1.27552 1.27462 1.27277]
CORTA 1  at close: 1.2727700000000002 2004-01-13 11:00:00
        OP CONTRARIA SE ABRE COMPRA 1  at close: 1.2727700000000002 2004-01-13 11:00:00
[1.2591  1.25951 1.25951 1.25869 1.2595  1.25955 1.25948 1.2591  1.25907
 1.25917 1.25911 1.25785 1.26029 1.25903 1.25943 1.25911 1.25909 1.25697
 1.2539  1.25461 1.25411 1.25454 1.2565  1.25733 1.25675 1.25535 1.25308
 1.2563  1.25607 1.25577 1.25698 1.25733 1.2591  1.26202 1.2619  1.26003
 1.25912 1.25999 1.26131 1.25846 1.25911 1.26    1.25916 1.25875 1.25904
 1.25832 1.26077 1.26318 1.26554 1.26569 1.26534 1.26605 1.26616 1.26554
 1.26634 1.26847 1.26354 1.26527 1.26662 1.26807 1.26709 1.26454 1.26661
 1.26717 1.26792 1.26833 1.26608 1.26696 1.2656  1.26753 1.26737 1.2683
 1.26805 1.26669 1.26818 1.26779 1.2677  1.26874 1.27033 1.27094 1.27127
 1.2721  1.27469 1.2741  1.27544 1.27952 1.27692 1.27456 1.27717 1.27669
 1.27626 1.27623 1.2739  1.27256 1.27257 1.2715  1.27192 1.27032 1.27068
 1

...

[1.2591  1.25951 1.25951 ... 1.30213 1.30225 1.30536]
LARGA 0  at close: 1.30536 2004-11-19 13:00:00
[1.2591  1.25951 1.25951 ... 1.30225 1.30536 1.30488]
LARGA 0  at close: 1.3048799999999998 2004-11-19 14:00:00
            HOLD 0  at close: 1.3048799999999998 2004-11-19 14:00:00 prev price 1.30536
[1.2591  1.25951 1.25951 ... 1.30536 1.30488 1.30553]
[1.2591  1.25951 1.25951 ... 1.30488 1.30553 1.30572]
-1 SELL with OP at close:  1.30572 2004-11-19 16:00:00
[1.2591  1.25951 1.25951 ... 1.30553 1.30572 1.30398]
CORTA 0  at close: 1.30398 2004-11-19 17:00:00
        HOLD 0  at close: 1.30398 2004-11-19 17:00:00
[1.2591  1.25951 1.25951 ... 1.30572 1.30398 1.30387]
CORTA -1  at close: 1.30387 2004-11-19 18:00:00
        VENTA -1  at close: 1.30387 2004-11-19 18:00:00
[1.2591  1.25951 1.25951 ... 1.30398 1.30387 1.30123]
CORTA 1  at close: 1.30123 2004-11-19 19:00:00
        OP CONTRARIA SE ABRE COMPRA 1  at close: 1.30123 2004-11-19 19:00:00
[1.2591  1.25951 1.25951 ... 1.30387 1.30123 

        HOLD 0  at close: 1.33055 2004-12-01 15:00:00
[1.2591  1.25951 1.25951 ... 1.33165 1.33055 1.3307 ]
CORTA 0  at close: 1.3307 2004-12-01 16:00:00
        HOLD 0  at close: 1.3307 2004-12-01 16:00:00
1.3307  price
1.33055  prev_price
            HOLD 0  at close: 1.3307 2004-12-01 16:00:00 prev price 1.33055
[1.2591  1.25951 1.25951 ... 1.33055 1.3307  1.3312 ]
[1.2591  1.25951 1.25951 ... 1.3307  1.3312  1.33178]
[1.2591  1.25951 1.25951 ... 1.3312  1.33178 1.33204]
[1.2591  1.25951 1.25951 ... 1.33178 1.33204 1.3323 ]
1 BUY without OP at close:  1.3323 2004-12-01 20:00:00
1 position:  <Position: 0>
[1.2591  1.25951 1.25951 ... 1.33204 1.3323  1.33427]
LARGA 0  at close: 1.33427 2004-12-01 21:00:00
[1.2591  1.25951 1.25951 ... 1.3323  1.33427 1.33374]
LARGA 0  at close: 1.33374 2004-12-01 22:00:00
            HOLD 0  at close: 1.33374 2004-12-01 22:00:00 prev price 1.33427
[1.2591  1.25951 1.25951 ... 1.33427 1.33374 1.33446]
1 BUY without OP at close:  1.33446 2004-12-01 23:00

CORTA 1  at close: 1.3281 2004-12-09 12:00:00
        OP CONTRARIA SE ABRE COMPRA 1  at close: 1.3281 2004-12-09 12:00:00
[1.2591  1.25951 1.25951 ... 1.32805 1.3281  1.32992]
LARGA 0  at close: 1.32992 2004-12-09 13:00:00
[1.2591  1.25951 1.25951 ... 1.3281  1.32992 1.32985]
LARGA -1  at close: 1.32985 2004-12-09 14:00:00
        OP CONTRARIA SE ABRE VENTA -1  at close: 1.32985 2004-12-09 14:00:00
[1.2591  1.25951 1.25951 ... 1.32992 1.32985 1.32562]
CORTA 0  at close: 1.32562 2004-12-09 15:00:00
        HOLD 0  at close: 1.32562 2004-12-09 15:00:00
[1.2591  1.25951 1.25951 ... 1.32985 1.32562 1.3263 ]
CORTA 0  at close: 1.3263 2004-12-09 16:00:00
        HOLD 0  at close: 1.3263 2004-12-09 16:00:00
1.3263  price
1.32562  prev_price
            HOLD 0  at close: 1.3263 2004-12-09 16:00:00 prev price 1.32562
[1.2591  1.25951 1.25951 ... 1.32562 1.3263  1.32697]
2 BUY without OP at close:  1.32697 2004-12-09 17:00:00
2 position:  <Position: 0>
[1.2591  1.25951 1.25951 ... 1.3263  1.3269

[1.2591  1.25951 1.25951 ... 1.33925 1.33902 1.33861]
[1.2591  1.25951 1.25951 ... 1.33902 1.33861 1.33935]
[1.2591  1.25951 1.25951 ... 1.33861 1.33935 1.3393 ]
[1.2591  1.25951 1.25951 ... 1.33935 1.3393  1.33885]
[1.2591  1.25951 1.25951 ... 1.3393  1.33885 1.3393 ]
[1.2591  1.25951 1.25951 ... 1.33885 1.3393  1.33982]
[1.2591  1.25951 1.25951 ... 1.3393  1.33982 1.33913]
[1.2591  1.25951 1.25951 ... 1.33982 1.33913 1.3395 ]
[1.2591  1.25951 1.25951 ... 1.33913 1.3395  1.33888]
[1.2591  1.25951 1.25951 ... 1.3395  1.33888 1.33911]
[1.2591  1.25951 1.25951 ... 1.33888 1.33911 1.3392 ]
-1 SELL with OP at close:  1.3392 2004-12-21 06:00:00
[1.2591  1.25951 1.25951 ... 1.33911 1.3392  1.33742]
CORTA -1  at close: 1.33742 2004-12-21 07:00:00
        VENTA -1  at close: 1.33742 2004-12-21 07:00:00
[1.2591  1.25951 1.25951 ... 1.3392  1.33742 1.33598]
CORTA 1  at close: 1.33598 2004-12-21 08:00:00
        OP CONTRARIA SE ABRE COMPRA 1  at close: 1.33598 2004-12-21 08:00:00
[1.2591  1.25951

Start                             0
End                            6239
Duration                       6239
Exposure [%]                71.3736
Equity Final [$]            58761.4
Equity Peak [$]             58787.3
Return [%]                  5776.14
Buy & Hold Return [%]       7.98825
Max. Drawdown [%]         -0.858879
Avg. Drawdown [%]        -0.0389985
Max. Drawdown Duration           21
Avg. Drawdown Duration      3.78252
# Trades                       2663
Win Rate [%]                98.9486
Best Trade [%]              1.58967
Worst Trade [%]           -0.703882
Avg. Trade [%]             0.152766
Max. Trade Duration               7
Avg. Trade Duration         1.67217
Expectancy [%]             0.154366
SQN                         37.1088
Sharpe Ratio                1.26674
Sortino Ratio               1.12595
Calmar Ratio               0.177866
_strategy                      MAW5
dtype: object

In [131]:
bt.plot()

In [114]:
values = []
def frange(start, stop=None, step=None):
    #Use float number in range() function

    # if stop and step argument is null set start=0.0 and step = 1.0
    if stop == None:
        stop = start + 0.0
        start = 0.0

    if step == None:
        step = 1.0

    while True:
        if step > 0 and start >= stop:
            break
        elif step < 0 and start <= stop:
            break
        yield ("%g" % start) # return float number
        start = start + step

print ("\n Using negative floating point numbers in range")
for i in frange(-0.00095, 0.0005, 0.0001):
    values.append(float(i))
    #rint (i, end=", ")
print(values)    


 Using negative floating point numbers in range
[-0.00095, -0.00085, -0.00075, -0.00065, -0.00055, -0.00045, -0.00035, -0.00025, -0.00015, -5e-05, 5e-05, 0.00015, 0.00025, 0.00035, 0.00045]


In [ ]:

    
%%time

stats = bt.optimize(VAR1=values, VAR2=values,
                    maximize='Equity Final [$]')
stats